In [2]:
import pandas as pd
import numpy as np
from pathlib import Path

In [18]:
ROOT = Path.cwd()
DATA_DIR = ROOT / "datasets"
IPEDS_DIR = DATA_DIR / "ipeds"
MIGRATION_DIR = IPEDS_DIR / "migration"
PROCESSED_DIR = IPEDS_DIR / "processed"

In [6]:
code_to_state = {     #dictionary of state codes to state, yes there are gaps
    "01": "Alabama",
    "02": "Alaska",
    "04": "Arizona",
    "05": "Arkansas",
    "06": "California",
    "08": "Colorado",
    "09": "Connecticut",
    "10": "Delaware",
    "11": "District of Columbia",
    "12": "Florida",
    "13": "Georgia",
    "15": "Hawaii",
    "16": "Idaho",
    "17": "Illinois",
    "18": "Indiana",
    "19": "Iowa",
    "20": "Kansas",
    "21": "Kentucky",
    "22": "Louisiana",
    "23": "Maine",
    "24": "Maryland",
    "25": "Massachusetts",
    "26": "Michigan",
    "27": "Minnesota",
    "28": "Mississippi",
    "29": "Missouri",
    "30": "Montana",
    "31": "Nebraska",
    "32": "Nevada",
    "33": "New Hampshire",
    "34": "New Jersey",
    "35": "New Mexico",
    "36": "New York",
    "37": "North Carolina",
    "38": "North Dakota",
    "39": "Ohio",
    "40": "Oklahoma",
    "41": "Oregon",
    "42": "Pennsylvania",
    "44": "Rhode Island",
    "45": "South Carolina",
    "46": "South Dakota",
    "47": "Tennessee",
    "48": "Texas",
    "49": "Utah",
    "50": "Vermont",
    "51": "Virginia",
    "53": "Washington",
    "54": "West Virginia",
    "55": "Wisconsin",
    "56": "Wyoming",
    "57": "Unknown",
    "58": "US Total"
}

In [5]:
migration = pd.read_csv(MIGRATION_DIR / "ef2000c.csv")
migration

unitid  line xefres01  efres01 xefres02  efres02
0      100858    45        R       42        R     39.0
1      102270    12        R       15        R     15.0
2      104531    31        R        1        R      1.0
3      106148    32        R        2        R      1.0
4      117113    98        G       94        B      NaN
...       ...   ...      ...      ...      ...      ...
62013  432232    12        R      149        R      0.0
62014  432232    98        G        0        B      NaN
62015  432232    99        G      149        G      0.0
62016  432241    41        R       38        R      0.0
62017  432241    98        G        0        B      NaN

[62018 rows x 6 columns]

In [ ]:
# getting unique IDs of schools in migration data
unique_schools = migration["unitid"].unique()


migrationIDs = migration["unitid"] # school ID
migrationState = migration["line"] # state code
migationStudents = migration["efres01"] # num first-time undergrad from that state

labels = ["unitid"] + [code_to_state.get(str(i).zfill(2), "DEFAULT") for i in range(1, 59)] + ["GRAND TOTAL"]

['unitid',
 'Alabama',
 'Alaska',
 'DEFAULT',
 'Arizona',
 'Arkansas',
 'California',
 'DEFAULT',
 'Colorado',
 'Connecticut',
 'Delaware',
 'District of Columbia',
 'Florida',
 'Georgia',
 'DEFAULT',
 'Hawaii',
 'Idaho',
 'Illinois',
 'Indiana',
 'Iowa',
 'Kansas',
 'Kentucky',
 'Louisiana',
 'Maine',
 'Maryland',
 'Massachusetts',
 'Michigan',
 'Minnesota',
 'Mississippi',
 'Missouri',
 'Montana',
 'Nebraska',
 'Nevada',
 'New Hampshire',
 'New Jersey',
 'New Mexico',
 'New York',
 'North Carolina',
 'North Dakota',
 'Ohio',
 'Oklahoma',
 'Oregon',
 'Pennsylvania',
 'DEFAULT',
 'Rhode Island',
 'South Carolina',
 'South Dakota',
 'Tennessee',
 'Texas',
 'Utah',
 'Vermont',
 'Virginia',
 'DEFAULT',
 'Washington',
 'West Virginia',
 'Wisconsin',
 'Wyoming',
 'Unknown',
 'US Total',
 'GRAND TOTAL']

In [47]:

# loop through each row in migration to assemble an array containing state makeups for each unique school in migration data, then appending it to a dataframe (OPTIMIZE IF TOO SLOW)

merged = []   # holds rows 

currIdx = 0         # current row in migration data

TOTAL_LABEL_COUNT = 60              # state codes go from 1-58 (with gaps) + 1 for all US studenmts + 1 for total students
LAST_IDX = TOTAL_LABEL_COUNT - 1    # last idx of row
GRAND_TOTAL_STATE_CODE = 99         # state code for grand total

for schoolID in unique_schools:
    row = migration.iloc[currIdx]
    outputRow = [float("nan")] * TOTAL_LABEL_COUNT   
    outputRow[0] = schoolID

    while (currIdx < len(migrationIDs) and schoolID == migrationIDs[currIdx]):
        if (migrationState[currIdx] < LAST_IDX):                                         
            outputRow[migrationState[currIdx]] = migationStudents[currIdx]
        elif (migrationState[currIdx] == GRAND_TOTAL_STATE_CODE):
            outputRow[LAST_IDX] = migationStudents[currIdx]

        currIdx += 1

    print(outputRow)
    if (pd.isna(outputRow[LAST_IDX])):
        print(type(outputRow))
        outputRow[LAST_IDX] = np.nansum(outputRow) - outputRow[0]
    print(outputRow)

    if (not outputRow[LAST_IDX] == 0): 
        merged.append(outputRow)

    continue



[np.int64(100858), nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, np.int64(42), nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]
<class 'list'>
[np.int64(100858), nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, np.int64(42), nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, np.float64(42.0)]
[np.int64(102270), nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, np.int64(15), nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan]
<cl

In [48]:
# create dataframe from newly created rows, drop columns without values, replace null w/ 0

school_states = pd.DataFrame(merged, columns=labels)
school_states = school_states.dropna(axis=1, how="all")
school_states = school_states.dropna(how="all")
school_states = school_states.fillna(0)

school_states

unitid  Alabama  Alaska  Arizona  Arkansas  California  Colorado  \
0    100858      0.0     0.0      0.0       0.0         0.0       0.0   
1    102270      0.0     0.0      0.0       0.0         0.0       0.0   
2    104531      0.0     0.0      0.0       0.0         0.0       0.0   
3    106148      0.0     0.0      0.0       0.0         0.0       0.0   
4    127024      0.0     0.0      0.0       0.0         0.0       0.0   
..      ...      ...     ...      ...       ...         ...       ...   
104  383297      0.0     0.0      0.0       0.0         0.0       0.0   
105  383312      0.0     0.0      0.0       0.0         0.0       0.0   
106  383321      0.0     0.0      0.0       0.0         0.0       0.0   
107  383367      0.0     0.0      0.0       0.0         0.0       0.0   
108  383376      0.0     0.0      0.0       0.0         0.0       0.0   

     Connecticut  District of Columbia  Florida  ...  Tennessee  Texas  Utah  \
0            0.0                   0.0      0.0  ...        0.0    0.0   0.0   
1            0.0                   0.0     15.0  ...        0.0    0.0   0.0   
2            0.0                   0.0      0.0  ...        0.0    0.0   0.0   
3            0.0                   0.0      0.0  ...        0.0    0.0   0.0   
4            0.0                   0.0      0.0  ...        0.0    0.0   0.0   
..           ...                   ...      ...  ...        ...    ...   ...   
104          0.0                   0.0      0.0  ...        0.0    0.0   0.0   
105          0.0                   0.0      0.0  ...        0.0    0.0   0.0   
106          0.0                   0.0      0.0  ...        0.0    0.0   0.0   
107          0.0                   0.0      0.0  ...        0.0    0.0   0.0   
108          0.0                   0.0      0.0  ...        0.0    0.0   0.0   

     Vermont  Virginia  Washington  Wisconsin  Wyoming  Unknown  GRAND TOTAL  
0        0.0       0.0         0.0        0.0      0.0      0.0         42.0  
1        0.0       0.0         0.0        0.0      0.0      0.0         15.0  
2        0.0       0.0         0.0        0.0      0.0      0.0          1.0  
3        0.0       0.0         0.0        0.0      0.0      0.0          2.0  
4        0.0       0.0         0.0        0.0      0.0      0.0          2.0  
..       ...       ...         ...        ...      ...      ...          ...  
104      0.0       0.0         0.0        0.0      0.0      0.0        118.0  
105      0.0       0.0         0.0        0.0      0.0      0.0         38.0  
106      0.0       0.0         0.0        0.0      0.0      0.0          6.0  
107      0.0       0.0         0.0        0.0      0.0      0.0        154.0  
108      0.0       0.0         0.0        0.0      0.0      0.0         42.0  

[109 rows x 48 columns]

In [ ]:
# add in grand total value for rows that don't have it (this data sucks)



In [19]:
# put files in it
out_file = PROCESSED_DIR / f"2000_crushed_migration.csv"
school_states.to_csv(out_file, index=False)